### Классификация по тональности
В этом домашнем задании вам предстоит классифицировать по тональности отзывы на банки с сайта banki.ru.

Данные содержат непосредственно тексты отзывов, некоторую дополнительную информацию, а также оценку по шкале от 1 до 5.

Тексты хранятся в json-ах в массиве responses.

Посмотрим на примере отзыва: возьмите для удобства ноутбук, размещенный в папке репозитория.


### Часть 1. Анализ текстов
1. Посчитайте количество отзывов в разных городах и на разные банки
2. Постройте гистограмы длин слов в символах и в словах
3. Найдите 10 самых частых:
- слов
- слов без стоп-слов
- лемм
- существительных

4. Постройте кривые Ципфа и Хипса
5. Ответьте на следующие вопросы:
- какое слово встречается чаще, "сотрудник" или "клиент"?
- сколько раз встречается слова "мошенничество" и "доверие"?

6. В поле "rating_grade" записана оценка отзыва по шкале от 1 до 5. Используйте меру $tf-idf$, для того, чтобы найти ключевые слова и биграмы для положительных отзывов (с оценкой 5) и отрицательных отзывов (с оценкой 1)

### Часть 2. Тематическое моделирование
1. Постройте несколько тематических моделей коллекции документов с разным числом тем. Приведите примеры понятных (интерпретируемых) тем.
2. Найдите темы, в которых упомянуты конкретные банки (Сбербанк, ВТБ, другой банк). Можете ли вы их прокомментировать / объяснить?
Эта часть задания может быть сделана с использованием gensim.

### Часть 3. Классификация текстов
Сформулируем для простоты задачу бинарной классификации: будем классифицировать на два класса, то есть, различать резко отрицательные отзывы (с оценкой 1) и положительные отзывы (с оценкой 5).

1. Составьте обучающее и тестовое множество: выберите из всего набора данных N1 отзывов с оценкой 1 и N2 отзывов с оценкой 5 (значение N1 и N2 – на ваше усмотрение). Используйте sklearn.model_selection.train_test_split для разделения множества отобранных документов на обучающее и тестовое.
2. Используйте любой известный вам алгоритм классификации текстов для решения задачи и получите baseline. Сравните разные варианты векторизации текста: использование только униграм, пар или троек слов или с использованием символьных $n$-грам.
3. Сравните, как изменяется качество решения задачи при использовании скрытых тем в качестве признаков:
- 1-ый вариант: $tf-idf$ преобразование (sklearn.feature_extraction.text.TfidfTransformer) и сингулярное разложение (оно же – латентый семантический анализ) (sklearn.decomposition.TruncatedSVD),
- 2-ой вариант: тематические модели LDA (sklearn.decomposition.LatentDirichletAllocation).
Используйте accuracy и F-measure для оценки качества классификации.

В ноутбуке, размещенном в папке репозитория. написан примерный Pipeline для классификации текстов.

Эта часть задания может быть сделана с использованием sklearn.


In [35]:
import json

import bz2                  # for compressing the data
import regex
from tqdm import tqdm
from scipy import sparse

from beholder import print_methods

In [28]:
import pandas as pd
import numpy as np
import nltk
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
%matplotlib inline
# %pylab inline

In [16]:
%%time
responses = []          # list of responses (dicts)
with bz2.BZ2File('/Users/velo1/SynologyDrive/GIT_syno/data/NLP/banki_responses.json.bz2', 'r') as thefile:
    for row in tqdm(thefile):
        resp = json.loads(row)  # convert from string to dict

        if not resp['rating_not_checked'] and (len(resp['text'].split()) > 0):
            responses.append(resp)  # add only non-empty responses and checked by moderators

201030it [01:18, 2550.99it/s]

CPU times: user 1min 17s, sys: 865 ms, total: 1min 18s
Wall time: 1min 18s



Посмотрим на пример отзыва:

In [15]:
responses[99]

{'city': 'г. Дзержинск (Нижегородская обл.)',
 'rating_not_checked': True,
 'title': 'Общий отзыв за 6 месяцев обслуживания в банке',
 'num_comments': 0,
 'bank_license': 'лицензия № 323',
 'author': 'maior2008',
 'bank_name': 'МДМ Банк',
 'datetime': '2015-06-05 19:27:52',
 'text': 'Минус номер 1 Перед новым годом я решил оформить карту в этом банке. Предварительно я прочитал информацию на сайте и в официальных документах. Я решил оформить продукт Дебетовая Добрая карта Мастер кард с бесплатным годовым обслуживанием по акции. Придя в банк и сев к свободному оператору, объяснил что мне нужно. Меня стали убеждать, что для получения карты необходимо внести сначала депозит на вклад в банк для новых клиентов. (Я такую информацию на сайте не видел) и сказал, что не имею наличных, на что получил ответ, что мы оформим карту и вы внесете вклад потом, задним числом. Придя домой и уточнив информацию в колл центре, мне сказали, что никакого вклада делать не надо. Придя в банк и рассказав им, сказ

In [17]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 153499 entries, 0 to 153498
Data columns (total 10 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   city                138325 non-null  object 
 1   rating_not_checked  153499 non-null  bool   
 2   title               153499 non-null  object 
 3   num_comments        153499 non-null  int64  
 4   bank_license        153498 non-null  object 
 5   author              153479 non-null  object 
 6   bank_name           153499 non-null  object 
 7   datetime            153499 non-null  object 
 8   text                153499 non-null  object 
 9   rating_grade        88658 non-null   float64
dtypes: bool(1), float64(1), int64(1), object(7)
memory usage: 10.7+ MB


In [18]:
data = pd.DataFrame(responses)
data.head()

city  rating_not_checked  \
0       г. Москва               False   
1  г. Новосибирск               False   
2       г. Москва               False   
3   г. Ставрополь               False   
4    г. Челябинск               False   

                                               title  num_comments  \
0                                             Жалоба             0   
1      Не могу пользоваться услугой Сбербанк он-лайн             0   
2                    Двойное списание за один товар.             1   
3  Меняют проценты комиссии  не предупредив и не ...             2   
4             Верните денежные средства за страховку             1   

      bank_license       author        bank_name             datetime  \
0  лицензия № 2562       uhnov1          Бинбанк  2015-06-08 12:50:54   
1  лицензия № 1481       Foryou  Сбербанк России  2015-06-08 11:09:57   
2  лицензия № 2562   Vladimir84          Бинбанк  2015-06-05 20:14:28   
3  лицензия № 1481       643609  Сбербанк России  2015-06-05 13:51:01   
4  лицензия № 2766  anfisa-2003         ОТП Банк  2015-06-05 10:58:12   

                                                text  rating_grade  
0  Добрый день! Я не являюсь клиентом банка и пор...           NaN  
1  Доброго дня! Являюсь держателем зарплатной кар...           NaN  
2  Здравствуйте!  Дублирую свое заявление от 03.0...           NaN  
3  Добрый день!! Я открыл расчетный счет в СберБа...           NaN  
4  04.03.2015 г. взяла кредит в вашем банке, заяв...           NaN

In [127]:
grouped_city = (
    data.groupby("city")
    .count()
    .sort_values(by="num_comments", ascending=False)
    .head(20)
)

fig = px.bar(
    grouped_city["num_comments"],
    x=grouped_banks.index,
    y="num_comments",
    title="Города с наибольшим количеством отзывов",
    width=1000,
    height=600,
    text_auto=True,
    color=grouped_city["num_comments"],
    color_continuous_scale="darkmint",
)
# fig.update_xaxes(autorange="reversed")

fig.update_layout(
    yaxis_title="Количество отзывов",
    xaxis_title="Город",
    showlegend=False
)
fig.update_layout(showlegend=False)
fig.show()

In [128]:
grouped_banks = (
    data.groupby("bank_name")
    .count()
    .sort_values(by="num_comments", ascending=False)
    .head(20)
)

fig = px.bar(
    grouped_banks,
    x=grouped_banks.index,
    y="num_comments",
    title="Количество отзывов по банкам",
    text_auto=True,
    hover_data=["num_comments"],
    color=grouped_banks.index,
    color_continuous_scale= "darkmint",
    height = 800
)
fig.update_xaxes(tickangle=45, title_text="Банк")
fig.update_yaxes(title_text="Количество отзывов")
fig.update_layout(showlegend=False)

fig.show()

## Классификация текстов

In [5]:
from sklearn.pipeline import Pipeline
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.decomposition import TruncatedSVD
from sklearn.ensemble import RandomForestClassifier

# !!! На каждом этапе Pipeline нужно указать свои параметры
# 1-ый вариант: tf-idf + LSI
# 2-ой вариант: LDA

# clf = Pipeline([
#     ('vect', CountVectorizer(analyzer = 'char', ngram_range={4,6})),
#     ('clf', RandomForestClassifier()),
# ])



clf = Pipeline([ 
    ('vect', CountVectorizer()), 
    ('tfidf', TfidfTransformer()), 
    ('tm', TruncatedSVD()), 
    ('clf', RandomForestClassifier())
])


In [6]:
text_data = [responses[i]['text'] for i in range(len(responses))    ]
# text_data = [re.sub(r'[^\w\s]','',text_data[i]) for i in range(len(text_data))    ]
# text_data = [re.sub(r'\d+','',text_data[i]) for i in range(len(text_data))    ]
# text_data = [text_data[i].lower() for i in range(len(text_data))    ]
# text_data = [text_data[i].split() for i in range(len(text_data))    ]
# text_data = [list(filter(None, text_data[i])) for i in range(len(text_data))    ]
# text_data = [list(filter(lambda x: x not in stop_words, text_data[i])) for i in range(len(text_data))    ]
# text_data = [list(filter(lambda x: x not in ['nan'], text_data[i])) for i in range(len(text_data))    ]

len(text_data), text_data

(153499,
 ['Добрый день! Я не являюсь клиентом банка и поручителем по кредитному договору, а также не являюсь каким-либо другим лицом, письменно  оформившим отношения с банком по поводу урегулирования чьей-либо  задолженности.  Начиная с марта 2015 года начали приходить бесконечные письма из ООО "Примо коллект"на мой адрес: город Москва, Уваровский переулок, дом 10, квартира 111, с угрозами о возбуждении уголовного дела в отношении гражданина Филиппова Эдуарда Владимировича, который уклоняется от уплаты взятых им кредитов: договор № 81014 от 20.10.2013 года и договор № 2464946 от 09.10.2014 года. Со всей ответственностью\xa0 хочу Вас заверить, что вышеуказанный гражданин, которого Вы разыскиваете, мне не знаком и никогда в моем адресе не был зарегистрирован. Каким образом Вы не удостоверившись в подлинности его документов оформили на его имя кредитный договор, мне по меньшей мере не понятно,\xa0 и почему по Вашей милости я должна переживать и бояться за себе и свое имущество. Письма до

In [7]:
text_data = [resp['text'] for resp in responses]
# text_data = [re.sub(r'[^\w\s]','',text_data[i]) for i in range(len(text_data))    ]
# text_data = [re.sub(r'\d+','',text_data[i]) for i in range(len(text_data))    ]
# text_data = [text_data[i].lower() for i in range(len(text_data))    ]
# text_data = [text_data[i].split() for i in range(len(text_data))    ]
# text_data = [list(filter(None, text_data[i])) for i in range(len(text_data))    ]
# text_data = [list(filter(lambda x: x not in stop_words, text_data[i])) for i in range(len(text_data))    ]
# text_data = [list(filter(lambda x: x not in ['nan'], text_data[i])) for i in range(len(text_data))    ]

len(text_data), text_data

(153499,
 ['Добрый день! Я не являюсь клиентом банка и поручителем по кредитному договору, а также не являюсь каким-либо другим лицом, письменно  оформившим отношения с банком по поводу урегулирования чьей-либо  задолженности.  Начиная с марта 2015 года начали приходить бесконечные письма из ООО "Примо коллект"на мой адрес: город Москва, Уваровский переулок, дом 10, квартира 111, с угрозами о возбуждении уголовного дела в отношении гражданина Филиппова Эдуарда Владимировича, который уклоняется от уплаты взятых им кредитов: договор № 81014 от 20.10.2013 года и договор № 2464946 от 09.10.2014 года. Со всей ответственностью\xa0 хочу Вас заверить, что вышеуказанный гражданин, которого Вы разыскиваете, мне не знаком и никогда в моем адресе не был зарегистрирован. Каким образом Вы не удостоверившись в подлинности его документов оформили на его имя кредитный договор, мне по меньшей мере не понятно,\xa0 и почему по Вашей милости я должна переживать и бояться за себе и свое имущество. Письма до